# Imports and Library Setup

This code block sets up the environment by importing all necessary libraries and modules required for the project. Below is a detailed explanation of each import:

## Standard Libraries
- **time**: Provides time-related functions, useful for measuring execution time or creating timestamps.
  
- **logging**: Enables configurable logging, which is essential for tracking the execution flow and debugging.

- **re**: Supports regular expression operations for pattern matching and text manipulation.

- **random**: Supplies functions to generate random numbers and make random selections, which can aid in data sampling and ensuring reproducibility.

- **gc**: Interfaces with Python’s garbage collection system, allowing manual memory management (e.g., freeing up unused memory).

## Data Processing Libraries
- **numpy (`np`)**: A fundamental package for numerical computations and handling multi-dimensional arrays.

- **pandas (`pd`)**: A powerful library for data manipulation and analysis, especially with DataFrame structures that handle tabular data efficiently.

## Deep Learning Libraries
- **torch**: PyTorch is used for tensor computations and building deep learning models. It supports GPU acceleration, which is crucial for training large models.

- **evaluate**: A library designed for model evaluation, offering standardized metrics to compare model outputs against reference data.

## Hugging Face Ecosystem
- **datasets (Dataset, DatasetDict, load_from_disk)**: 
  - *Dataset*: Represents a single dataset, allowing for efficient data manipulation.

  - *DatasetDict*: A container to hold multiple datasets (e.g., train, test, validation splits).

  - *load_from_disk*: Facilitates loading previously saved datasets, which helps in preserving preprocessing efforts.

- **transformers**: A library for working with state-of-the-art pre-trained models and tokenizers.
  - **AutoModelForSeq2SeqLM**: Automatically loads a model suited for sequence-to-sequence tasks (e.g., translation, summarization).


  - **AutoTokenizer**: Automatically loads the appropriate tokenizer for the chosen model.


  - **TrainingArguments**: Encapsulates all the hyperparameters and configurations needed for training a model.


  - **Trainer**: Provides an easy-to-use interface for training, evaluating, and performing predictions with models.


  - **GenerationConfig**: Allows configuration of parameters for text generation, such as max token limits or beam search settings.


  - **BitsAndBytesConfig**: Configures low-bit quantization settings, enabling efficient fine-tuning and inference with reduced precision.

- **EarlyStoppingCallback (from transformers.trainer_callback)**: Implements early stopping during training to prevent overfitting and save computational resources.

## PEFT (Parameter-Efficient Fine-Tuning)
- **LoraConfig**: Configures Low-Rank Adaptation (LoRA), a method for fine-tuning large models efficiently by updating only a small subset of parameters.

- **get_peft_model**: Applies the PEFT method to a base model, integrating LoRA layers into it.

- **prepare_model_for_kbit_training**: Prepares a model for training with low-bit (quantized) precision, optimizing memory usage and computational efficiency.

---

These imports collectively provide all the functionalities needed for:
- Data handling and preprocessing.

- Loading and configuring state-of-the-art models.

- Fine-tuning using efficient techniques like LoRA.

- Evaluating model performance with standardized metrics.

This robust setup forms the backbone for building, training, and evaluating sequence-to-sequence models tailored for tasks such as text-to-SQL conversion.


In [1]:
import time
import logging
import re
import random
import gc
import numpy as np
import pandas as pd
import torch
import evaluate

from datasets import Dataset, DatasetDict, load_from_disk
from transformers import (
    AutoModelForSeq2SeqLM,
    AutoTokenizer,
    TrainingArguments,
    Trainer,
    GenerationConfig,
    BitsAndBytesConfig,
)
from transformers.trainer_callback import EarlyStoppingCallback
from peft import LoraConfig, get_peft_model, prepare_model_for_kbit_training

# Device and Computation Optimization Setup

This block of code is dedicated to optimizing the runtime performance and ensuring that computations are performed on the most suitable hardware.

## Enabling cuDNN Benchmark

- **Purpose:**

    - Enables cuDNN benchmarking in PyTorch to automatically select the fastest algorithm for the given fixed input sizes.

- **Benefit:**

    - Can significantly speed up computations, particularly for operations like convolutions in deep learning models when input dimensions remain constant.

## Setting the Computation Device

- **Device Selection:**

    - Checks if a CUDA-compatible GPU is available. If so, it sets the device to "cuda" otherwise, it defaults to the CPU.

- **Output:**

    - The print(device) statement confirms which device is selected.

- **Impact:**

    - Utilizing a GPU when available can dramatically accelerate model training and inference by leveraging parallel processing capabilities.


In [2]:
# Enable cudnn benchmark for fixed input sizes (can speed up computation)
torch.backends.cudnn.benchmark = True

# Set device to RTX 4090
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(device)

cuda


# Setting Random Seeds for Reproducibility

This block of code sets a fixed random seed across multiple libraries to ensure that experiments and model training are reproducible. Consistent seeding is crucial for debugging, comparing model performance, and sharing reproducible research.

- **random.seed(42):**
Sets the seed for Python's built-in random module. This ensures that any random numbers generated using this module (e.g., for data shuffling or random sampling) remain consistent across runs.

- **np.random.seed(42):**
Sets the seed for NumPy's random number generator. Since NumPy is widely used for numerical operations and generating random arrays, this makes sure that any randomness in these operations is controlled.

- **torch.manual_seed(42):**
Sets the seed for PyTorch's CPU-based random number generator. This is essential for ensuring that model initialization and any other operations involving randomness in PyTorch produce the same results in every run.

- **torch.cuda.manual_seed_all(42):**
Ensures that all random operations on GPUs (like random weight initialization or dropout) are also deterministic.

- **Overall Impact:**
By fixing the seed value (42 in this case) across all relevant libraries (Python's random, NumPy, and PyTorch for both CPU and GPU), this code block guarantees that the entire pipeline produces the same results on every run, thus enhancing reproducibility and reliability in experiments.

In [3]:
random.seed(42)
np.random.seed(42)
torch.manual_seed(42)
if torch.cuda.is_available():
    torch.cuda.manual_seed_all(42)

# Memory Clearing Utility Function

This function is designed to free up system and GPU memory during runtime. It is especially useful in scenarios where you are working with large datasets or deep learning models, as it helps mitigate memory leaks and prevents out-of-memory errors.

- **`gc.collect()`:**
Invokes Python’s garbage collector to identify and free up memory that is no longer in use.
This step helps in cleaning up any residual objects that are not referenced, ensuring efficient memory management on the CPU.

- **`torch.cuda.empty_cache()`:**
Clears the cached memory allocated by PyTorch on the GPU.
Although PyTorch reuses cached memory to improve performance, manually clearing the cache can be beneficial when switching between models or after heavy memory usage, as it makes more GPU memory available for subsequent operations.



In [4]:
def clear_memory():
    gc.collect()
    torch.cuda.empty_cache()

# Logging Configuration Setup

This block configures the Python logging module to ensure that log messages are informative and consistently formatted across the application. Here's a detailed breakdown:

- **`logging.basicConfig(...)`:**
Sets up the basic configuration for the logging system:

- **`level=logging.INFO`:**
Specifies that the logging level is set to INFO. This means that all log messages with a severity of INFO, WARNING, ERROR, or CRITICAL will be captured and displayed. Debug messages (DEBUG level) will be ignored unless the level is set to DEBUG.


- **`format="%(asctime)s - %(levelname)s - %(message)s"`:**
Defines the format of the log messages:
    - **`%(asctime)s`:** Inserts a timestamp into each log message, which helps in tracking when each event occurred.
    
    - **`%(levelname)s`:** Inserts the log level (e.g., INFO, WARNING) of the message, providing insight into the severity or importance of the logged event.
    
    - **`%(message)s`:** Inserts the actual log message content.


- **`logger = logging.getLogger(__name__)`:**
Retrieves a logger instance specific to the current module:

**`__name__`** is a special Python variable that holds the name of the current module. This ensures that the logger is uniquely identified by the module's name, making it easier to locate log messages in larger applications with multiple modules.
The returned logger object is then used to log messages throughout the module with methods like logger.info(), logger.error(), etc.

### Overall, this setup standardizes logging across the application, making it easier to monitor the program's behavior, debug issues, and record the sequence of events during execution.

In [5]:
logging.basicConfig(
    level=logging.INFO,
    format="%(asctime)s - %(levelname)s - %(message)s",
)
logger = logging.getLogger(__name__)

# Data Cleaning Utility Functions

This block defines two functions essential for preparing and cleaning text data within pandas DataFrames. These functions help standardize text fields and ensure DataFrame columns are properly formatted for subsequent processing or model training.

---

## Function: `preprocess`

### Explanation:

- **Purpose:**
The preprocess function is designed to clean a text string by removing unnecessary whitespace and newline characters, ensuring that the text is formatted consistently.

- **Input Parameter:**

    - `text (str)`: The text string to be cleaned.

- **Functionality:**

    - **Type Check:**
        The function first checks if the input is a string. If it is not, it returns an empty string to avoid processing invalid data.

    - **Newline Replacement:**
        The `text.replace('\n', ' ')` part converts newline characters into spaces, flattening the text into a single line.

    - **Whitespace Reduction:**
        The `re.sub(r'\s+', ' ', ...)` call uses a regular expression to replace multiple consecutive whitespace characters (spaces, tabs, etc.) with a single space.

    - **Trimming:**
        Finally, `.strip()` removes any leading or trailing whitespace from the resulting string.
### Output:
**A cleaned string with extra spaces and newline characters removed.**


In [6]:
def preprocess(text: str) -> str:
    """Remove extra whitespaces and newlines from a text string."""
    if not isinstance(text, str):
        return ""
    return re.sub(r'\s+', ' ', text.replace('\n', ' ')).strip()

def clean_df(df, rename=None, drop=None, select=None):
    """
    Clean and rename dataframe columns:
      - drop: list of columns to drop
      - rename: dict mapping old column names to new names
      - select: list of columns to keep in final order
    """
    if drop:
        df = df.drop(columns=drop, errors='ignore')
    if rename:
        df = df.rename(columns=rename)
    for col in ['query', 'context', 'response']:
        if col in df.columns:
            df[col] = df[col].apply(preprocess)
    if select:
        df = df[select]
    return df

# Loading, Cleaning, and Merging Raw Datasets

This code block handles the entire process of loading raw datasets from various sources, cleaning and standardizing their columns, and merging them into a single DataFrame ready for further processing. Below is a detailed explanation of each step:

1. **Logging the Start of Dataset Loading:**
   This log message indicates that the process of loading the datasets is about to begin, providing visibility into the workflow execution.

2. **Loading Datasets**

3. **Cleaning and Standardizing Column Names:**
   To ensure consistency across all datasets, each DataFrame is cleaned using the clean_df function, which:
    - Renames columns to a unified naming convention (query, context, response).
    
    - Drops unnecessary columns.
    
    - Applies text preprocessing to remove extraneous whitespaces and newlines.

4. **Concatenating DataFrames:**
    - All the cleaned DataFrames are merged into a single DataFrame (final_df) using pd.concat, which resets the index.
    
    - A log statement records the total number of rows in the merged DataFrame before any duplicates are removed.

5. **Final DataFrame Cleanup:**
    - **Column Reordering:**
          The DataFrame is restructured to enforce a specific column order: query, context, and response.
    
    - **Dropping Missing Values:**
          Any rows that have missing values in these critical columns are removed using dropna().
    
    - **Removing Duplicates:**
          Duplicate rows are dropped to ensure each example is unique.

A final log statement records the number of rows remaining after cleaning, providing a clear picture of the dataset size for subsequent steps.

### Overall, these steps ensure that diverse raw datasets are uniformly processed, cleaned, and merged into a coherent format, ready for tokenization and model training.

In [7]:
logger.info("Loading raw datasets from various sources...")

# Load datasets
df1 = pd.read_json("hf://datasets/Clinton/Text-to-sql-v1/texttosqlv2.jsonl", lines=True)
df2 = pd.read_json("hf://datasets/b-mc2/sql-create-context/sql_create_context_v4.json")
df3 = pd.read_parquet("hf://datasets/gretelai/synthetic_text_to_sql/synthetic_text_to_sql_train.snappy.parquet")
df4 = pd.read_json("hf://datasets/knowrohit07/know_sql/know_sql_val3{ign}.json")

# Clean and rename columns to unify to 'query', 'context', 'response'
df1 = clean_df(df1, rename={'instruction': 'query', 'input': 'context'}, drop=['source', 'text'])
df2 = clean_df(df2, rename={'question': 'query', 'answer': 'response'})
df3 = clean_df(df3, rename={'sql_prompt': 'query', 'sql_context': 'context', 'sql': 'response'},
                select=['query', 'context', 'response'])
df4 = clean_df(df4, rename={'question': 'query', 'answer': 'response'})

# Concatenate all DataFrames
final_df = pd.concat([df1, df2, df3, df4], ignore_index=True)
logger.info("Total rows before dropping duplicates: %d", len(final_df))

# Force correct column order and drop rows with missing fields
final_df = final_df[['query', 'context', 'response']]
final_df = final_df.dropna(subset=['query', 'context', 'response'])
final_df = final_df.drop_duplicates()
logger.info("Total rows after dropping duplicates: %d", len(final_df))

2025-03-19 14:56:53,295 - INFO - Loading raw datasets from various sources...
2025-03-19 14:57:25,655 - INFO - Total rows before dropping duplicates: 490241
2025-03-19 14:57:27,208 - INFO - Total rows after dropping duplicates: 440785


# Tokenizer Initialization and Token Length Filtering

This block of code prepares the tokenizer and filters the merged DataFrame (`final_df`) based on token length constraints for both prompts and responses. Here’s a detailed breakdown:

1. **Tokenizer Initialization:**
    - **Purpose:**
        Loads the pre-trained tokenizer corresponding to the "`google/flan-t5-base`" model. This tokenizer will be used to convert text (prompts and responses) into token IDs required by the model.
    
    - **Context:**
        Using a pre-trained tokenizer ensures that text is tokenized in a manner consistent with the model’s training, which is essential for achieving good performance.
2. **Setting Maximum Token Lengths:**
    - **Purpose:**
        These variables define the maximum allowed token lengths for the prompt and response respectively.
    
    - **Benefit:**
        Enforcing token limits prevents overly long inputs that could lead to out-of-memory errors or inefficient processing. The limits are chosen based on model constraints and expected input sizes.
3. **Defining the Token Length Filter Function:**
    - **Purpose:**
        This function evaluates each row of the DataFrame to determine if its prompt and response, once tokenized, fit within the predefined token limits.
    
    - **Steps within the Function:**
        - **Prompt Construction:**
            Combines the context and query fields from the row with designated markers (`"Context:"`, `"Query:"`, `"Response:"`) to create a full prompt.
        
        - **Tokenization:**
            The prompt and response are tokenized without truncation (truncation=False) to capture the full token count.
            add_special_tokens=True ensures that any model-specific tokens (like start-of-sequence or end-of-sequence tokens) are included.
        
        - **Token Length Check:**
            The function returns True if both the prompt and response have token counts within their respective limits, otherwise False.
4. **Filtering the DataFrame:**
    - **Purpose:**
        Applies the tokenize_length_filter function to each row of final_df and filters out any rows that do not meet the token length constraints.
    
    - **Result:**
        The resulting DataFrame contains only those rows where both the prompt and the response are within the acceptable token lengths.
5. **Logging the Result:**
    - **Purpose:**
        Logs the number of rows remaining in the DataFrame after applying the token length filter.
    
    - **Benefit:**
        This log statement provides insight into how much data remains after filtering, which is useful for monitoring and debugging the preprocessing pipeline.

### Overall Impact: 
    - By initializing the tokenizer and filtering based on token length, this code ensures that the inputs provided to the model are within manageable sizes, thus preventing errors during training or inference and ensuring efficient processing.

In [8]:
tokenizer = AutoTokenizer.from_pretrained("google/flan-t5-base")

max_length_prompt = 500
max_length_response = 250

def tokenize_length_filter(row):
    start_prompt = "Context:\n"
    middle_prompt = "\n\nQuery:\n"
    end_prompt = "\n\nResponse:\n"
    
    # Construct the prompt as used in the tokenize_function
    prompt = f"{start_prompt}{row['context']}{middle_prompt}{row['query']}{end_prompt}"
    
    # Encode without truncation to get the full token count
    prompt_tokens = tokenizer.encode(prompt, add_special_tokens=True, truncation=False)
    response_tokens = tokenizer.encode(row['response'], add_special_tokens=True, truncation=False)
    
    return len(prompt_tokens) <= max_length_prompt and len(response_tokens) <= max_length_response

final_df = final_df[final_df.apply(tokenize_length_filter, axis=1)]
logger.info("Total rows after filtering by token length (prompt <= %d and response <= %d tokens): %d", 
            max_length_prompt, max_length_response, len(final_df))


Token indices sequence length is longer than the specified maximum sequence length for this model (1113 > 512). Running this sequence through the model will result in indexing errors
2025-03-19 15:01:13,787 - INFO - Total rows after filtering by token length (prompt <= 500 and response <= 250 tokens): 398481


In [9]:
logger.info("Sample from filtered final_df:\n%s", final_df.head(3))
clear_memory()

2025-03-19 15:01:13,794 - INFO - Sample from filtered final_df:
                                               query  \
0           Name the home team for carlton away team   
1  what will the population of Asia be when Latin...   
2  How many faculty members do we have for each g...   

                                             context  \
0  CREATE TABLE table_name_77 ( home_team VARCHAR...   
1  CREATE TABLE table_22767 ( "Year" real, "World...   
2  CREATE TABLE Student ( StuID INTEGER, LName VA...   

                                            response  
0  SELECT home_team FROM table_name_77 WHERE away...  
1  SELECT "Asia" FROM table_22767 WHERE "Latin Am...  
2  SELECT Sex, COUNT(*) FROM Faculty GROUP BY Sex...  


# Splitting DataFrame into Train, Test, and Validation Sets and Converting to Hugging Face Dataset

This code block is responsible for dividing the cleaned DataFrame (`final_df`) into training, testing, and validation subsets, and then converting these splits into Hugging Face Datasets for further processing.

---

1. **Splitting the DataFrame:**

    - **Function Purpose:**
    The `split_dataframe` function divides a DataFrame into three distinct subsets:

        - **Training Set:** Contains 85% of the data (by default).
    
        - **Test Set:** Contains 10% of the data.
    
        - **Validation Set:** Contains the remaining 5% of the data.

    - **Detailed Steps:**

        - **Determine Total Rows:**
            - `n = len(df)` calculates the total number of rows in the DataFrame.

        - **Calculate Split Indices:**
            - **`train_end = int(n * train_frac)`** determines the index where the training data should end.
        
            - **`test_end = train_end + int(n * test_frac)`** calculates the index where the test data should end, immediately following the training set.

        - **Slice the DataFrame:**
            - **`train_df = df.iloc[:train_end].reset_index(drop=True)`** selects the training portion and resets the index.
        
            - **`test_df = df.iloc[train_end:test_end].reset_index(drop=True)`** selects the test portion and resets the index.
        
            - **`val_df = df.iloc[test_end:].reset_index(drop=True)`** selects the validation portion and resets the index.
          
        - **Return Splits:**
            The function returns the three DataFrame splits.
 
2. **Converting DataFrame Splits to Hugging Face Datasets:**

    - **Conversion Process:**
        Each pandas DataFrame (`train_df`, `test_df`, `val_df`) is converted into a Hugging Face `Dataset` using `Dataset.from_pandas()`. This allows efficient manipulation and processing during training and evaluation.

    - **Dataset Dictionary:**
        A `DatasetDict` is created to organize the datasets under clearly labeled splits: `'train'`, `'test'`, and `'validation'`. This standard structure is widely used in Hugging Face pipelines.

3. **Saving the Dataset to Disk and Memory Cleanup:**

    - **Saving:**
        `dataset.save_to_disk("merged_dataset")` saves the merged dataset to disk. This ensures that the preprocessed data is persisted and can be reloaded in future sessions without repeating the preprocessing steps.

    - **Logging:**
        Log messages confirm that the dataset has been successfully merged, saved, and provide a summary of its structure.

    - **Memory Cleanup:**
        `clear_memory()` is called to free up any residual memory, which is especially important after handling large datasets.

### Overall Impact:

**This entire code block streamlines the data preparation process by:**

    - Splitting the dataset into train, test, and validation sets.
    
    - Converting these splits into a format compatible with Hugging Face's ecosystem.
    
    - Saving the processed dataset for efficient future reuse.
    
    - Logging key information and cleaning up memory to maintain optimal performance.

In [10]:
def split_dataframe(df, train_frac=0.85, test_frac=0.1, val_frac=0.05):
    n = len(df)
    train_end = int(n * train_frac)
    test_end = train_end + int(n * test_frac)
    train_df = df.iloc[:train_end].reset_index(drop=True)
    test_df = df.iloc[train_end:test_end].reset_index(drop=True)
    val_df = df.iloc[test_end:].reset_index(drop=True)
    return train_df, test_df, val_df

train_df, test_df, val_df = split_dataframe(final_df)
logger.info("Final split sizes: Train: %d, Test: %d, Validation: %d", len(train_df), len(test_df), len(val_df))

# Convert splits to Hugging Face Datasets
train_dataset = Dataset.from_pandas(train_df)
test_dataset = Dataset.from_pandas(test_df)
val_dataset = Dataset.from_pandas(val_df)

dataset = DatasetDict({
    'train': train_dataset,
    'test': test_dataset,
    'validation': val_dataset
})

dataset.save_to_disk("merged_dataset")
logger.info("Merged and Saved Dataset Successfully!")
logger.info("Dataset summary: %s", dataset)
clear_memory()

2025-03-19 15:01:14,006 - INFO - Final split sizes: Train: 338708, Test: 39848, Validation: 19925


Saving the dataset (0/1 shards):   0%|          | 0/338708 [00:00<?, ? examples/s]

Saving the dataset (0/1 shards):   0%|          | 0/39848 [00:00<?, ? examples/s]

Saving the dataset (0/1 shards):   0%|          | 0/19925 [00:00<?, ? examples/s]

2025-03-19 15:01:15,490 - INFO - Merged and Saved Dataset Successfully!
2025-03-19 15:01:15,497 - INFO - Dataset summary: DatasetDict({
    train: Dataset({
        features: ['query', 'context', 'response'],
        num_rows: 338708
    })
    test: Dataset({
        features: ['query', 'context', 'response'],
        num_rows: 39848
    })
    validation: Dataset({
        features: ['query', 'context', 'response'],
        num_rows: 19925
    })
})


# Reloading and Tokenizing the Dataset for T5 Fine-Tuning

This code block covers several critical steps to prepare the dataset for fine-tuning a T5 model. It includes reloading a previously merged dataset from disk, initializing the tokenizer, defining a custom tokenization function, and finally either loading an existing tokenized version or creating one if it doesn't exist. Below is a detailed explanation of each part of the code:

---

1. **Reloading the Dataset from Disk:**
    - **Purpose:**
      The merged dataset, previously saved under the name `"merged_dataset"`, is reloaded using the `load_from_disk function`.
        
    - **Logging:**
      A sample from the test split of the reloaded dataset is logged. This helps verify that the dataset was loaded correctly and gives a quick glance at the structure of the data.

2. **Initializing the Tokenizer:**
    - **Purpose:**
        - Sets the model name to `"google/flan-t5-base"`, which corresponds to the pre-trained T5 model.
        
        - Loads the associated tokenizer using `AutoTokenizer.from_pretrained`, ensuring that tokenization is consistent with how the model was originally trained.

3. **Defining the Tokenization Function:**

    - **Function Overview:**
        - The `tokenize_function` prepares a batch of examples for T5 fine-tuning by constructing a standardized prompt and tokenizing both the prompt and its corresponding response.

    - **Prompt Construction:**
        - Three strings (`start_prompt`, `middle_prompt`, and `end_prompt`) define the structure of the prompt.
        
        - Each example’s prompt is created by combining the `context` and `query` fields from the batch with these fixed markers.
          
    - **Tokenization of Inputs and Labels:**
        - **Prompts:**
            - The constructed prompts are tokenized with a maximum length of 512 tokens, using padding and truncation to ensure uniformity.
        
        - **Responses:**
            - The responses are tokenized separately with a maximum length of 256 tokens.

        - **Label Preparation:**
            - Tokenized responses are processed so that any token matching the pad token ID is replaced with `-100`. This ensures that the loss function will ignore these padded positions during training.

    - **Updating the Batch:**
        - **The function adds three keys to the batch dictionary:**
            - `'input_ids'`: The tokenized prompt IDs.
            
            - `'attention_mask'`: The attention masks corresponding to the prompts.
            
            - `'labels'`: The processed tokenized responses.

        - **The updated batch is then returned.**

4. **Loading or Creating the Tokenized Dataset:**

    - **Purpose:**
        - The code attempts to load a pre-tokenized version of the dataset from disk, saved under the name `"tokenized_datasets"`.

    - **Error Handling:**
        - If the tokenized dataset is not found (which throws an exception), the code logs that it will create a new tokenized dataset.

    - **Dataset Mapping:**
        - Uses the map function on the original dataset with the `tokenize_function`:

        - **Batched Processing:**
            - `batched=True` allows processing multiple examples at once for efficiency.

        - **Removing Unnecessary Columns:**
            - The original columns query, context, and response are removed after tokenization since they are no longer needed.

        - **Parallel Processing:**
            - `num_proc=8` utilizes 8 processes to speed up the tokenization.

    - **Saving:**
        - The newly tokenized dataset is saved to disk as `"tokenized_datasets"` for future reuse.

        - Appropriate log messages are generated to confirm the process.
     
5. **Formatting and Logging the Final Tokenized Dataset:**

    - **Setting the Format:**
        - `tokenized_datasets.set_format("torch")` converts the dataset into a PyTorch-compatible format, which is necessary for efficient training.

    - **Logging the Dataset Structure:**
        - The keys of the tokenized dataset (typically `'train'`, `'test'`, and `'validation'`) are logged to verify the available splits.
    
        - A sample record from the training split is also logged to ensure that the tokenization was successful and the data is formatted as expected.

### Overall Impact:
    - This comprehensive block of code efficiently reloads, tokenizes, and formats the dataset for T5 fine-tuning. 
    
    - It leverages robust error handling to either load an existing tokenized dataset or generate a new one when necessary, ensuring that the subsequent training process will proceed smoothly with data in the correct format.




In [11]:
dataset = load_from_disk("merged_dataset")
logger.info("Reloaded dataset from disk. Example from test split:\n%s", dataset['test'][0])

model_name = "google/flan-t5-base"
tokenizer = AutoTokenizer.from_pretrained(model_name)

def tokenize_function(batch: dict) -> dict:
    """
    Tokenizes a batch of examples for T5 fine-tuning.
    Constructs a prompt in the format:
      Context:
      <context>
      
      Query:
      <query>
      
      Response:
    """
    start_prompt = "Context:\n"
    middle_prompt = "\n\nQuery:\n"
    end_prompt = "\n\nResponse:\n"

    prompts = [
        f"{start_prompt}{ctx}{middle_prompt}{qry}{end_prompt}"
        for ctx, qry in zip(batch['context'], batch['query'])
    ]

    tokenized_inputs = tokenizer(
        prompts,
        padding="max_length",
        truncation=True,
        max_length=512
    )
    tokenized_labels = tokenizer(
        batch['response'],
        padding="max_length",
        truncation=True,
        max_length=256
    )
    labels = [
        [-100 if token == tokenizer.pad_token_id else token for token in seq]
        for seq in tokenized_labels['input_ids']
    ]

    batch['input_ids'] = tokenized_inputs['input_ids']
    batch['attention_mask'] = tokenized_inputs['attention_mask']
    batch['labels'] = labels
    return batch

try:
    tokenized_datasets = load_from_disk("tokenized_datasets")
    logger.info("Loaded Tokenized Dataset from disk.")
except Exception as e:
    logger.info("Tokenized dataset not found. Creating a new one...")
    tokenized_datasets = dataset.map(
        tokenize_function,
        batched=True,
        remove_columns=['query', 'context', 'response'],
        num_proc=8
    )
    tokenized_datasets.save_to_disk("tokenized_datasets")
    logger.info("Tokenized and Saved Dataset.")

tokenized_datasets.set_format("torch")

logger.info("Final tokenized dataset splits: %s", tokenized_datasets.keys())
logger.info("Sample tokenized record from train split:\n%s", tokenized_datasets['train'][0])

2025-03-19 15:01:15,843 - INFO - Reloaded dataset from disk. Example from test split:
{'query': "Show the name and type of military cyber commands in the 'Military_Cyber_Commands' table.", 'context': "CREATE SCHEMA IF NOT EXISTS defense_security;CREATE TABLE IF NOT EXISTS defense_security.Military_Cyber_Commands (id INT PRIMARY KEY, command_name VARCHAR(255), type VARCHAR(255));INSERT INTO defense_security.Military_Cyber_Commands (id, command_name, type) VALUES (1, 'USCYBERCOM', 'Defensive Cyber Operations'), (2, 'JTF-CND', 'Offensive Cyber Operations'), (3, '10th Fleet', 'Network Warfare');", 'response': 'SELECT command_name, type FROM defense_security.Military_Cyber_Commands;'}
2025-03-19 15:01:16,155 - INFO - Loaded Tokenized Dataset from disk.
2025-03-19 15:01:16,159 - INFO - Final tokenized dataset splits: dict_keys(['train', 'test', 'validation'])
2025-03-19 15:01:16,167 - INFO - Sample tokenized record from train split:
{'input_ids': tensor([ 1193,  6327,    10,   205,  4386,  6

# Baseline Zero-Shot Generation Using the Pre-Trained T5 Model

This code demonstrates how to perform zero-shot text generation using the pre-trained T5 model ("google/flan-t5-base"). The process involves loading the model and its tokenizer, selecting a sample from the test dataset, constructing a prompt, generating a response with the model, and finally printing both the human-provided response and the model's output. Additionally, the memory is cleared at the end to manage GPU resources efficiently.

---

1. ***Model and Tokenizer Initialization:***
   
    - ***Model Name:***
        - The variable model_name is set to `"google/flan-t5-base"`, indicating the specific pre-trained T5 model being used.

    - ***Tokenizer Initialization:***
        - The tokenizer corresponding to the T5 model is loaded using `AutoTokenizer.from_pretrained()`. This ensures that the text is tokenized in a manner consistent with the model’s training.

    - ***Model Loading:***
        - The T5 model is loaded with the data type `torch.bfloat16` for improved memory efficiency and performance on compatible hardware.

    - ***Device Assignment:***
        - The model is moved to the computation device (GPU or CPU) specified by the variable `device` to leverage hardware acceleration.
          
2. ***Selecting a Test Example:***

    - ***Purpose:***
        - A single example (at index 0) is selected from the test split of the dataset.

    - ***Data Extraction:***
        - The `query`, `context`, and `response` fields are extracted from the chosen test example. These fields represent the input query, accompanying context, and the human-provided response respectively.

3. ***Constructing the Input Prompt***

    - ***Prompt Format:***
        - A multi-line formatted string (f-string) is created to structure the input prompt.

        - The prompt is divided into three parts:
            - Context: Introduced by the line `"Context:"` followed by the actual context.

            - Query: Introduced by `"Query:"` followed by the query.

            - Response: A label `"Response:"` which indicates where the model should generate its answer.
    
    - ***Purpose:***
        - This structured prompt format guides the model during text generation by clearly delineating the context and query sections.
         
4. ***Tokenizing the Prompt and Generating Output***

    - ***Tokenization:***
        - The prompt is tokenized using the tokenizer. The parameter `return_tensors='pt'` ensures that the output is in PyTorch tensor format, suitable for model processing.

        - The tokenized inputs are moved to the device (GPU/CPU) for computation.

    - ***Text Generation:***
        - The model's `generate()` method is called on the tokenized `input_ids` to produce output tokens. The parameter `max_new_tokens=200` sets a limit on the number of tokens the model can generate.

    - ***Decoding:***
        - The generated tokens are decoded back into a human-readable string using `tokenizer.decode()`. The parameter `skip_special_tokens=True` removes any special tokens (e.g., `<pad>`, `<eos>`) from the output.

5. ***Displaying the Input and Output:***

    - ***Visual Separation:***
        - A dashed line is created (`dash_line`) for clear visual separation of the output sections.

    - ***Output Sections:***
        - The constructed input prompt is printed.

        - The human-provided (baseline) response is printed, serving as a reference.
     
        - The model-generated output is printed, representing the zero-shot generation result.
     
6. ***Memory Cleanup***

    - ***Purpose:***
        - The `clear_memory()` function is called to release unused GPU memory. This is essential in managing resources efficiently, especially after performing memory-intensive operations like model inference.

### Overall Impact:

    - This code block establishes a baseline for zero-shot text generation with the T5 model. 
    
    - By clearly structuring the prompt, tokenizing input, and generating a response, it sets the stage for comparing the model's performance against human responses. 
    
    - The process, along with memory management practices, ensures that the system runs efficiently during inference.


In [12]:
model_name = 'google/flan-t5-base'
tokenizer = AutoTokenizer.from_pretrained(model_name)
original_model = AutoModelForSeq2SeqLM.from_pretrained(model_name, torch_dtype=torch.bfloat16)
original_model = original_model.to(device)

index = 0
query = dataset['test'][index]['query']
context = dataset['test'][index]['context']
response = dataset['test'][index]['response']

prompt = f"""Context:
{context}

Query:
{query}

Response:
"""
inputs = tokenizer(prompt, return_tensors='pt').to(device)
baseline_output = tokenizer.decode(
    original_model.generate(
        inputs["input_ids"],
        max_new_tokens=200,
    )[0],
    skip_special_tokens=True
)
dash_line = '-' * 100
print(dash_line)
print(f'INPUT PROMPT:\n{prompt}')
print(dash_line)
print(f'BASELINE HUMAN ANSWER:\n{response}\n')
print(dash_line)
print(f'MODEL GENERATION - ZERO SHOT:\n{baseline_output}')
clear_memory()

----------------------------------------------------------------------------------------------------
INPUT PROMPT:
Context:
CREATE SCHEMA IF NOT EXISTS defense_security;CREATE TABLE IF NOT EXISTS defense_security.Military_Cyber_Commands (id INT PRIMARY KEY, command_name VARCHAR(255), type VARCHAR(255));INSERT INTO defense_security.Military_Cyber_Commands (id, command_name, type) VALUES (1, 'USCYBERCOM', 'Defensive Cyber Operations'), (2, 'JTF-CND', 'Offensive Cyber Operations'), (3, '10th Fleet', 'Network Warfare');

Query:
Show the name and type of military cyber commands in the 'Military_Cyber_Commands' table.

Response:

----------------------------------------------------------------------------------------------------
BASELINE HUMAN ANSWER:
SELECT command_name, type FROM defense_security.Military_Cyber_Commands;

----------------------------------------------------------------------------------------------------
MODEL GENERATION - ZERO SHOT:
USCYBERCOM, JTF-CND, Offensive Cyber Op

# Fine-Tuning Setup with QLORA: Detailed Explanation

This section is dedicated to setting up and launching the fine-tuning process using a QLORA-based approach. The code first attempts to load an already fine-tuned model from disk; if it isn’t available, it initializes the base model with QLORA modifications for efficient parameter-efficient fine-tuning. The following detailed explanation breaks down every part of the code:

---

1. ***Attempting to Load the Fine-Tuned Model:***

    - ***Objective:***
        - The code first attempts to load an existing fine-tuned model (`text2sql_flant5base_finetuned`) from disk.

    - ***Steps:***
        - ***Logging:***
            - A log message indicates the attempt to load the fine-tuned model.

        - ***Loading the Model:***
            - `AutoModelForSeq2SeqLM.from_pretrained("text2sql_flant5base_finetuned")` loads the model that has already been fine-tuned.

        - ***Tokenizer Initialization:***
            - The corresponding tokenizer is loaded using the base model identifier (`google/flan-t5-base`).

        - ***Device Assignment:***
            - The model is moved to the computation device (GPU/CPU) specified by the variable `device`.

        - ***Training Flag:***
            - The variable `to_train` is set to `False`, indicating that fine-tuning is not required if the model is already available.
 
        - ***Confirmation Logging:***
            - A log message confirms that the fine-tuned model was successfully loaded.

        - ***If the fine-tuned model is not found, the code enters the `except` block.***

            - ***Actions Taken:***

                - ***Logging:***
                  
                    - The absence of the fine-tuned model is logged.

                    - A subsequent log message indicates that the process is shifting to initialize the base model for QLORA fine-tuning.
                
                - ***Training Flag:***
                    - `to_train` is set to `True`, signifying that the fine-tuning process will commence.

2. ***QLORA-Specific Model Initialization:***

    - ***Setting Up Quantization Configuration:***
        - ***Purpose:***
            - ***Quantization with BitsAndBytes:***
                - The `BitsAndBytesConfig` is used to configure the model for 4-bit quantization. This is crucial for reducing memory usage and speeding up fine-tuning while maintaining model performance.
            
        - ***Parameters:***
            - ***`load_in_4bit=True`:***
                - Instructs the library to load the model in 4-bit precision.      
            
            - ***`bnb_4bit_quant_type="nf4"`:***
                - Specifies the quantization type. NF4 is a specific quantization scheme that optimizes the trade-off between precision and efficiency.

  
            - ***`bnb_4bit_use_double_quant=True`:***
                - Enables double quantization, which can improve quantization quality.
        
            - ***`bnb_4bit_compute_dtype=torch.bfloat16`:***
                - Sets the compute data type to `bfloat16`, offering a balance between speed and numerical stability.
           
    - ***Loading the Base Model with Quantization:***
        - ***Purpose:***
            - ***Loading the Base Model:***
                - The base T5 model is loaded with the quantization configuration applied. This means the model is prepared to operate in a lower-precision (4-bit) environment.

        - ***Key Parameters:***
            - ***`quantization_config=quant_config`:***
                - Applies the quantization settings defined earlier.

            - ***`device_map="auto"`:***
                - Automatically assigns parts of the model to available devices, which is especially useful for large models.
            - ***`torch_dtype=torch.bfloat16`:***
                - Ensures that the model computations use the `bfloat16` data type, optimizing for performance on compatible hardware.

    - ***Preparing the Model for k-Bit Training:***

        - ***Purpose:***
            - This function call further prepares the model to be fine-tuned in a low-bit (quantized) setting.

        - ***Impact:***
            - It typically involves adjustments such as modifying certain layers or parameters to better support k-bit (in this case, 4-bit) precision during training.

    - ***Configuring LoRA (Low-Rank Adaptation):***
        - ***Purpose:***
            - ***Parameter-Efficient Fine-Tuning (PEFT):***
                - LoRA is a method to fine-tune large language models efficiently by injecting trainable low-rank adaptation matrices into the model’s weights. This reduces the number of parameters that need to be updated during training.
        
        - ***Parameters Explained:***
            - ***`r=32`:***
                - The rank of the LoRA matrices. A higher rank allows for more expressiveness but at the cost of additional parameters.

            - ***`lora_alpha=64`:***
                - A scaling factor that balances the impact of the LoRA updates relative to the original weights.

            - ***`target_modules=["q", "v"]`:***
                - Specifies that only the query and value projection matrices in the model will be adapted using LoRA. This focuses the fine-tuning on key components of the transformer architecture.

            - ***`lora_dropout=0.1`:***
                - Applies a dropout rate of 10% to the LoRA layers to prevent overfitting.

            - ***`bias="none"`:***
                - Indicates that no bias terms will be added or modified in the LoRA layers.

            - ***`task_type="SEQ_2_SEQ_LM"`:***
                - Specifies that the task is sequence-to-sequence language modeling, which tailors the LoRA modifications to this setting.

    - ***Integrating LoRA with the Model:***

        - ***Purpose:***
            - ***PEFT Integration:***
                - The `get_peft_model` function wraps the base model with the LoRA configuration. This integrates the low-rank adapters into the model, allowing efficient fine-tuning by updating only a small subset of parameters.
        
        - ***Impact:***
            - This step is critical in reducing the computational cost and memory footprint during training, making it feasible to fine-tune large models on limited hardware.

    - ***Logging and Memory Cleanup:***

        - ***Logging:***
            - A log message confirms that the base model has been successfully loaded and is ready for QLORA fine-tuning.

        - ***Memory Cleanup:***
            - `clear_memory()` is called to free up any unused memory, which is especially important after loading and modifying large models.

3. ***Initiating the Training Process (if Required):***

    - Condition:
        - The training process is only initiated if `to_train` is `True` (i.e., when no fine-tuned model was found, and the model has been prepared for QLORA fine-tuning).
    
    - Output Directory:
        - An output directory is dynamically created using the current timestamp to ensure unique directory names for each training session.
    
    - Logging:
        - A log message confirms the start of the training process and displays the output directory path.

    - ***Calculating Training Steps and Warmup Steps:***

        - ***Purpose:***
            - Computes the total number of training steps based on:
            
            - The number of training samples.

            - The per-device training batch size.

            - The total number of training epochs.

            - Warmup steps are set to 10% of the total steps to gradually ramp up the learning rate at the beginning of training.
         
        - ***Math Operations:***
            - `math.ceil()` ensures that the number of steps is rounded up to cover all training samples.

        - ***Logging:***
            - Logs provide visibility into the total training and warmup steps.

    - ***Setting Up Training Arguments:***
  
        - ***Purpose:***
            - This block creates a `TrainingArguments` object that encapsulates all hyperparameters and training configurations.
    
        - ***Key Hyperparameters and Strategies:***
            - ***`out_dir`:***
                - Where the model checkpoints and logs will be saved.

            - ***`gradient_checkpointing`:***
                - Enabled to reduce memory usage by storing only necessary activations.

            - ***`gradient_accumulation_steps`:***
                - Accumulates gradients over multiple steps (2 in this case) to simulate a larger batch size.

            - ***`Learning Rate and Optimizer`:***
                - `learning_rate=2e-4` is set with the `optim=adamw_bnb_8bit`, a memory-efficient version of AdamW.
            
            - ***`per_device_train_batch_size` and `per_device_train_batch_size`:***
                - Specifies per-device batch sizes for both training and evaluation.

            - ***`weight_decay`:***
                - A regularization parameter to prevent overfitting.

            - ***Logging and Evaluation Strategies:***
                - Logging occurs every 200 steps.
                
                - Evaluation and model saving occur at the end of each epoch.
         
            - ***Checkpoint Management:***
                - Limits the total number of saved checkpoints to 3.
                
                - Automatically loads the best model at the end of training based on evaluation loss.
                  
            - ***Mixed Precision:***
                - `bf16` is enabled to leverage bfloat16 precision for faster computation with minimal loss in accuracy.
            
            - ***Learning Rate Scheduler:`lr_scheduler_type`***
                - A cosine scheduler is used, along with a warmup ratio of 10% of the total steps.
    
    - ***Creating the Trainer and Launching Training:***
        - ***Trainer Initialization:***
            - ***A `Trainer` object is created with:***
                - The QLORA-prepared `finetuned_model`.

                - The training arguments defined earlier.

                - The training and validation datasets.

                - A callback (`EarlyStoppingCallback`) that stops training if the evaluation loss does not improve for 2 consecutive epochs.

        - ***Training Execution:***
            - The training process is started using `trainer.train()`, and log messages provide feedback before and after training.

    - ***Saving the Fine-Tuned Model and Final Cleanup:***
        - ***Model Saving:***
            - After training, the fine-tuned model is saved to disk under the path `"text2sql_flant5base_finetuned"`.

        - ***Logging and Cleanup:***
            - A log message confirms that the model has been saved successfully.
            - The `clear_memory()` function is called to release any unused GPU memory.


In [13]:
import math

try:
    logger.info("Attempting to load the fine-tuned model...")
    finetuned_model = AutoModelForSeq2SeqLM.from_pretrained("text2sql_flant5base_finetuned")
    tokenizer = AutoTokenizer.from_pretrained("google/flan-t5-base")
    finetuned_model = finetuned_model.to(device)
    to_train = False
    logger.info("Fine-tuned model loaded successfully.")
except Exception as e:
    logger.info("Fine-tuned model not found.")
    logger.info("Initializing model and tokenizer for QLORA fine-tuning...")
    to_train = True

    quant_config = BitsAndBytesConfig(
        load_in_4bit=True,
        bnb_4bit_quant_type="nf4",
        bnb_4bit_use_double_quant=True,
        bnb_4bit_compute_dtype=torch.bfloat16,
    )

    finetuned_model = AutoModelForSeq2SeqLM.from_pretrained(
        model_name,
        quantization_config=quant_config,
        device_map="auto",
        torch_dtype=torch.bfloat16,
    )
    finetuned_model = prepare_model_for_kbit_training(finetuned_model)
    
    lora_config = LoraConfig(
        r=32,
        lora_alpha=64,
        target_modules=["q", "v"],
        lora_dropout=0.1,
        bias="none",
        task_type="SEQ_2_SEQ_LM"
    )
    finetuned_model = get_peft_model(finetuned_model, lora_config)
    tokenizer = AutoTokenizer.from_pretrained(model_name)
    logger.info("Base model loaded and prepared for QLORA fine-tuning.")
    clear_memory()

if to_train:
    output_dir = f"./sql-training-{int(time.time())}"
    logger.info("Starting training. Output directory: %s", output_dir)

    # Compute total training steps:
    num_train_samples = len(tokenized_datasets["train"])
    per_device_train_batch_size = 64
    per_device_eval_batch_size = 64
    num_train_epochs = 6
    # Assuming no gradient accumulation beyond the per-device batch size
    total_steps = math.ceil(num_train_samples / per_device_train_batch_size) * num_train_epochs
    # Set warmup steps as 10% of total steps (adjust as needed)
    warmup_steps = int(total_steps * 0.1)
    
    logger.info("Total training steps: %d, Warmup steps (10%%): %d", total_steps, warmup_steps)
    
    training_args = TrainingArguments(
        output_dir=output_dir,
        gradient_checkpointing=True,
        gradient_checkpointing_kwargs={"use_reentrant": True},
        gradient_accumulation_steps = 2,
        learning_rate=2e-4,
        optim="adamw_bnb_8bit",  # Memory-efficient optimizer
        num_train_epochs=num_train_epochs,
        per_device_train_batch_size=per_device_train_batch_size,
        per_device_eval_batch_size=per_device_eval_batch_size,
        weight_decay=0.01,
        logging_steps=200, 
        logging_dir=f"{output_dir}/logs",
        eval_strategy="epoch",  # Evaluate at the end of each epoch
        save_strategy="epoch",  # Save the model at the end of each epoch
        save_total_limit=3,
        load_best_model_at_end=True,
        metric_for_best_model="eval_loss",
        bf16=True,  
        warmup_ratio=0.1,  # Warmup 10% of total steps
        lr_scheduler_type="cosine",
    )
    trainer = Trainer(
        model=finetuned_model,
        args=training_args,
        train_dataset=tokenized_datasets["train"],
        eval_dataset=tokenized_datasets["validation"],
        callbacks=[EarlyStoppingCallback(early_stopping_patience=2)],
    )
    logger.info("Beginning fine-tuning...")
    trainer.train()
    logger.info("Training completed.")
    save_path = "text2sql_flant5base_finetuned"
    finetuned_model.save_pretrained(save_path)
    logger.info("Model saved to %s", save_path)
    clear_memory()

2025-03-19 15:01:30,827 - INFO - Attempting to load the fine-tuned model...
2025-03-19 15:01:32,195 - INFO - Fine-tuned model loaded successfully.


# Evaluation Pipeline: Detailed Explanation

This code segment implements a comprehensive pipeline for evaluating the performance of both an original (baseline) and a fine-tuned T5 model on a text-to-SQL task. It covers helper function definitions, example-based inference, batch evaluation over the entire test set, and computation of multiple evaluation metrics. Below is an in-depth explanation of every component:

---

1. ***Helper Functions for Post-Processing, Generation, and Evaluation:***

    - ***`post_process_output`:***
        - ***Purpose:***
            - This function processes the raw text generated by the model to ensure it contains only a single, complete SQL query.

        - ***Mechanism:***
            - It splits the output text at the first semicolon (`;`).

            - If a semicolon is found, only the portion before (and including) it is returned. Otherwise, the entire output is returned.

    - ***`generate_with_params`:***
        - ***Purpose:***
            - This helper function wraps the model's `generate()` method to produce text outputs with specified generation parameters.

        - ***Parameters Explained:***
            - ***`max_new_tokens=100`:***
                - Limits the number of tokens to generate.

            - ***`num_beams=5`:***
                - Uses beam search with 5 beams for better-quality outputs.

            - ***`repetition_penalty=1.2`:***
                - Penalizes repetitive token generation.

            - ***`temperature=0.1`:***
                - Low temperature makes the output more deterministic.

            - ***`early_stopping=True`:***
                - Stops generation as soon as the end-of-sequence token is produced.
        
        - ***Post-Processing:***
            - After generation, the output tokens are decoded into a string, and special tokens are skipped.
    
    - ***`normalize_sql`:***
        - ***Purpose:***
            - Converts SQL queries into a normalized form by lowercasing and removing extra spaces, facilitating fair comparisons between predictions and references.

    - ***`compute_exact_match`:***
        - ***Purpose:***
            - Calculates the percentage of predictions that exactly match the corresponding reference queries after normalization.

        - ***Mechanism:***
            - Compares each pair of normalized predictions and references; computes the ratio of exact matches.
         
    - ***`compute_fuzzy_match`:***
        - ***Purpose:***
            - Computes an average fuzzy matching score, which accounts for partial matches between generated queries and references.

        - ***Mechanism:***
            - Uses `fuzz.token_set_ratio` to score similarity for each prediction-reference pair and averages the results.

2. ***Part A: Inference on 5 Examples (Qualitative Evaluation):***

    - ***Extracting Samples from the Test Set:***
        - ***Purpose:***
            - Retrieves the first 5 examples from the test split, extracting the `query`, `context`, and `response` fields for each sample.

    - ***Looping Through Each Example for Inference:***
        - ***Process Overview:***
            - ***Prompt Construction:***
                - For each example, a prompt is built by concatenating the context and query with headers (`"Context:"`, `"Query:"`, and `"Response:"`) to instruct the model.

            - ***Tokenization:***
                - The prompt is tokenized into PyTorch tensors with a maximum length of 512 tokens and moved to the designated device.

            - ***Generation:***
                - The original model produces an output using `generate_with_params()`.

                - The fine-tuned model output is post-processed using `post_process_output()` to remove any repetitions.

            - ***Output Display:***
                - For each example, the input prompt, human response, original model output, and fine-tuned model output are printed with visual dividers.

            - ***Memory Management:***
                - The `clear_memory()` function is called after processing each example to maintain optimal resource usage.

3. ***Part B: Evaluation on the Full Test Set with Batching (Quantitative Evaluation):***

    - ***Initializing Response Lists and Batch Size:***
        - ***Purpose:***
            - Initializes lists to store the human-provided responses, and the outputs from both the original and fine-tuned models.
            - Sets the batch size for processing the test dataset in chunks (here, 128 examples per batch).
    
    - ***Processing the Test Set in Batches:***
        - ***Steps:***
            - ***Batch Slicing:***
                - The test dataset is processed in batches using slicing, which returns a dictionary of lists for each field (e.g., context, query, response).

            - ***Prompt Construction:***
                - For each example in the batch, a prompt is constructed in the same format as in Part A.

            - ***Response Collection:***
                - Human responses from the batch are collected into `all_human_responses`.

            - ***Tokenization:***
                - The batch of prompts is tokenized with padding and truncation (max length 512) and moved to the device.

            - ***Generation:***
                - Both models generate outputs for the entire batch using the same generation parameters as before.
            
            - ***Decoding and Post-Processing:***
                - The generated token IDs are decoded into strings. For the fine-tuned model, the output is post-processed to ensure only the first valid SQL query is retained.
            
            - ***Extending Response Lists:***
                - The decoded outputs are added to the corresponding response lists.

            - ***Memory Management:***
                - The `clear_memory()` function is called after each batch to maintain resource efficiency.

    - ***Creating and Saving a Comparison DataFrame:***
        - ***Purpose:***
            - Zips together human responses, original model outputs, and fine-tuned model outputs into a list of tuples.
            
            - Creates a pandas DataFrame from the zipped list, allowing for easy visualization and comparison.
            
            - Saves the DataFrame to a CSV file (`evaluation_results.csv`) for further analysis.
            
            - Calls `clear_memory()` to free resources.
         
4. ***Computing Evaluation Metrics:***

    - ***Computing Metrics for Original and Fine-tuned Model:***
        - ***Details:***
            - ***`ROUGE`:***
                - Evaluates the overlap of n-grams between predictions and references. Options like use_aggregator and use_stemmer help produce a more robust score.

            - ***`BLEU`:***
                - Computes precision-based scores by comparing the generated text to one or more reference texts.

            - ***`Fuzzy Matching`:***
                - Uses the custom compute_fuzzy_match function (with rapidfuzz) to measure soft similarity.

            - ***`Exact Match`:***
                - Uses the compute_exact_match function to calculate the percentage of predictions that exactly match the references after normalization.

        - ***The results of the evaluation metrics for both models are printed in a formatted output.***
            - This provides a clear quantitative assessment of the improvements (or differences) between the original and fine-tuned models.

In [14]:
import logging
import re
import pandas as pd
from rapidfuzz import fuzz
import evaluate

# Assuming tokenizer, device, original_model, finetuned_model, and dataset are already defined.
# Define a helper function for output post-processing.
def post_process_output(output_text: str) -> str:
    """Post-process the generated output to remove repeated text."""
    # Keep only the first valid SQL query (everything before the first semicolon)
    return output_text.split(";")[0] + ";" if ";" in output_text else output_text

# Define a helper function for generating outputs with the given generation parameters.
def generate_with_params(model, input_ids):
    generated_ids = model.generate(
        input_ids=input_ids,
        max_new_tokens=100, 
        num_beams=5,
        repetition_penalty=1.2,
        temperature=0.1,
        early_stopping=True
    )
    # Decode and post-process output
    output_text = tokenizer.decode(generated_ids[0], skip_special_tokens=True)
    return output_text

# Helper functions for SQL normalization and evaluation metrics
def normalize_sql(sql):
    """Normalize SQL by stripping whitespace and lowercasing."""
    return " ".join(sql.strip().lower().split())

def compute_exact_match(predictions, references):
    """Computes the exact match accuracy after normalization."""
    matches = sum(1 for pred, ref in zip(predictions, references)
                  if normalize_sql(pred) == normalize_sql(ref))
    return (matches / len(predictions)) * 100 if predictions else 0

def compute_fuzzy_match(predictions, references):
    """Computes a soft matching score using token_set_ratio from rapidfuzz."""
    scores = [fuzz.token_set_ratio(pred, ref) for pred, ref in zip(predictions, references)]
    return sum(scores) / len(scores) if scores else 0

# Dummy function to free up memory if needed.
def clear_memory():
    # If using torch.cuda, you can clear cache:
    # torch.cuda.empty_cache()
    pass

logger = logging.getLogger(__name__)
logger.setLevel(logging.INFO)

# --- Part A: Inference on 5 Examples with Real Responses ---
logger.info("Running inference on 5 examples (displaying real responses).")

num_examples = 5
sample_queries = dataset["test"][:num_examples]["query"]
sample_contexts = dataset["test"][:num_examples]["context"]
sample_human_responses = dataset["test"][:num_examples]["response"]

print("\n" + "=" * 100)
for idx in range(num_examples):
    prompt = f"""Context:
{sample_contexts[idx]}

Query:
{sample_queries[idx]}

Response:
"""
    # Tokenize the prompt and move to device
    inputs = tokenizer(prompt, return_tensors="pt", truncation=True, max_length=512).to(device)
    
    # Generate outputs using the modified generation parameters
    orig_out = generate_with_params(original_model, inputs["input_ids"])
    finetuned_out = post_process_output(generate_with_params(finetuned_model, inputs["input_ids"]))
    
    print("-" * 100)
    print(f"Example {idx+1}")
    print("-" * 100)
    print("INPUT PROMPT:")
    print(prompt)
    print("-" * 100)
    print("HUMAN RESPONSE:")
    print(sample_human_responses[idx])
    print("-" * 100)
    print("ORIGINAL MODEL OUTPUT:")
    print(orig_out)
    print("-" * 100)
    print("FINE-TUNED MODEL OUTPUT:")
    print(finetuned_out)
    print("=" * 100 + "\n")
    clear_memory()

# --- Part B: Evaluation on Full Test Set with Batching (Optimized) ---
logger.info("Starting evaluation on the full test set using batching.")

all_human_responses = []
all_original_responses = []
all_finetuned_responses = []

batch_size = 128  # Adjust based on GPU memory
test_dataset = dataset["test"]

for i in range(0, len(test_dataset), batch_size):
    # Slicing the dataset returns a dict of lists
    batch = test_dataset[i:i + batch_size]
    
    # Construct prompts for each example in the batch
    prompts = [
        f"Context:\n{batch['context'][j]}\n\nQuery:\n{batch['query'][j]}\n\nResponse:"
        for j in range(len(batch["context"]))
    ]
    
    # Extend human responses
    all_human_responses.extend(batch["response"])
    
    # Tokenize the batch of prompts with padding and truncation
    inputs = tokenizer(prompts, return_tensors="pt", padding=True, truncation=True, max_length=512).to(device)
    
    # Generate outputs for the batch for both models
    orig_ids = original_model.generate(
        input_ids=inputs["input_ids"],
        max_new_tokens=100,
        num_beams=5,
        repetition_penalty=1.2,
        temperature=0.1,
        early_stopping=True
    )
    finetuned_ids = finetuned_model.generate(
        input_ids=inputs["input_ids"],
        max_new_tokens=100,
        num_beams=5,
        repetition_penalty=1.2,
        temperature=0.1,
        early_stopping=True
    )
    
    # Decode and post-process each sample in the batch
    orig_texts = [tokenizer.decode(ids, skip_special_tokens=True) for ids in orig_ids]
    finetuned_texts = [post_process_output(tokenizer.decode(ids, skip_special_tokens=True)) for ids in finetuned_ids]
    
    all_original_responses.extend(orig_texts)
    all_finetuned_responses.extend(finetuned_texts)
    clear_memory()

# Create a DataFrame for a quick comparison of results
zipped_all = list(zip(all_human_responses, all_original_responses, all_finetuned_responses))
df_full = pd.DataFrame(zipped_all, columns=["Human Response", "Original Model Output", "Fine-Tuned Model Output"])
df_full.to_csv('evaluation_results.csv', index=False)
clear_memory()

# --- Compute Evaluation Metrics ---
rouge = evaluate.load("rouge")
bleu = evaluate.load("bleu")

# Compute metrics for the original (non-fine-tuned) model
orig_rouge = rouge.compute(
    predictions=all_original_responses,
    references=all_human_responses,
    use_aggregator=True,
    use_stemmer=True,
)
orig_bleu = bleu.compute(
    predictions=all_original_responses,
    references=[[ref] for ref in all_human_responses]
)
orig_fuzzy = compute_fuzzy_match(all_original_responses, all_human_responses)
orig_exact = compute_exact_match(all_original_responses, all_human_responses)

# Compute metrics for the fine-tuned model
finetuned_rouge = rouge.compute(
    predictions=all_finetuned_responses,
    references=all_human_responses,
    use_aggregator=True,
    use_stemmer=True,
)
finetuned_bleu = bleu.compute(
    predictions=all_finetuned_responses,
    references=[[ref] for ref in all_human_responses]
)
finetuned_fuzzy = compute_fuzzy_match(all_finetuned_responses, all_human_responses)
finetuned_exact = compute_exact_match(all_finetuned_responses, all_human_responses)

print("\n" + "=" * 100)
print("Evaluation Metrics:")
print("=" * 100)
print("ORIGINAL MODEL:")
print(f"  ROUGE: {orig_rouge}")
print(f"  BLEU: {orig_bleu}")
print(f"  Fuzzy Match Score: {orig_fuzzy:.2f}%")
print(f"  Exact Match Accuracy: {orig_exact:.2f}%\n")
print("FINE-TUNED MODEL:")
print(f"  ROUGE: {finetuned_rouge}")
print(f"  BLEU: {finetuned_bleu}")
print(f"  Fuzzy Match Score: {finetuned_fuzzy:.2f}%")
print(f"  Exact Match Accuracy: {finetuned_exact:.2f}%")
print("=" * 100)
clear_memory()

2025-03-19 15:01:32,235 - INFO - Running inference on 5 examples (displaying real responses).
/venv/main/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:629: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(



----------------------------------------------------------------------------------------------------
Example 1
----------------------------------------------------------------------------------------------------
INPUT PROMPT:
Context:
CREATE SCHEMA IF NOT EXISTS defense_security;CREATE TABLE IF NOT EXISTS defense_security.Military_Cyber_Commands (id INT PRIMARY KEY, command_name VARCHAR(255), type VARCHAR(255));INSERT INTO defense_security.Military_Cyber_Commands (id, command_name, type) VALUES (1, 'USCYBERCOM', 'Defensive Cyber Operations'), (2, 'JTF-CND', 'Offensive Cyber Operations'), (3, '10th Fleet', 'Network Warfare');

Query:
Show the name and type of military cyber commands in the 'Military_Cyber_Commands' table.

Response:

----------------------------------------------------------------------------------------------------
HUMAN RESPONSE:
SELECT command_name, type FROM defense_security.Military_Cyber_Commands;
------------------------------------------------------------------

2025-03-19 15:01:40,448 - INFO - Starting evaluation on the full test set using batching.


----------------------------------------------------------------------------------------------------
Example 5
----------------------------------------------------------------------------------------------------
INPUT PROMPT:
Context:
CREATE TABLE WindFarms (FarmID INT, FarmName VARCHAR(255), Capacity DECIMAL(5,2), Country VARCHAR(255)); INSERT INTO WindFarms (FarmID, FarmName, Capacity, Country) VALUES (1, 'WindFarm1', 150, 'USA'), (2, 'WindFarm2', 200, 'Canada'), (3, 'WindFarm3', 120, 'Mexico');

Query:
List the total installed capacity of wind farms in the WindEnergy schema for each country?

Response:

----------------------------------------------------------------------------------------------------
HUMAN RESPONSE:
SELECT Country, SUM(Capacity) as TotalCapacity FROM WindFarms GROUP BY Country;
----------------------------------------------------------------------------------------------------
ORIGINAL MODEL OUTPUT:
1, 150, USA, 2, 200, Canada, 3, 120, Mexico
---------------------

2025-03-19 16:47:58,173 - INFO - Using default tokenizer.
2025-03-19 16:49:07,668 - INFO - Using default tokenizer.



Evaluation Metrics:
ORIGINAL MODEL:
  ROUGE: {'rouge1': np.float64(0.05646642898660111), 'rouge2': np.float64(0.01562815013068162), 'rougeL': np.float64(0.05031267225420556), 'rougeLsum': np.float64(0.05036072587316542)}
  BLEU: {'bleu': 0.003142147128241449, 'precisions': [0.12293406776920406, 0.03289697910893642, 0.018512080104175887, 0.008342750223825794], 'brevity_penalty': 0.11177079327444009, 'length_ratio': 0.3133514352662089, 'translation_length': 377251, 'reference_length': 1203923}
  Fuzzy Match Score: 13.98%
  Exact Match Accuracy: 0.00%

FINE-TUNED MODEL:
  ROUGE: {'rouge1': np.float64(0.7538800834024002), 'rouge2': np.float64(0.6103863808522726), 'rougeL': np.float64(0.7262841884754194), 'rougeLsum': np.float64(0.7261852209847466)}
  BLEU: {'bleu': 0.4719774431701209, 'precisions': [0.7603153442288385, 0.598309257795389, 0.5021259810303533, 0.42128998564638875], 'brevity_penalty': 0.8474086962179814, 'length_ratio': 0.8579477258927689, 'translation_length': 1032903, 'refe

# Inference:

In [15]:
import torch
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer
import logging

# Set up logging
logging.basicConfig(
    level=logging.INFO,
    format="%(asctime)s - %(levelname)s - %(message)s",
)
logger = logging.getLogger(__name__)

# Ensure device is set (GPU if available)
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load the fine-tuned model and tokenizer
model_name = "text2sql_flant5base_finetuned" 
finetuned_model = AutoModelForSeq2SeqLM.from_pretrained(model_name, torch_dtype=torch.bfloat16)
tokenizer = AutoTokenizer.from_pretrained("google/flan-t5-base")
finetuned_model.to(device)

def run_inference(prompt_text: str) -> str:
    """
    Runs inference on the fine-tuned model using deterministic decoding
    with beam search, returning the generated SQL query.
    """
    inputs = tokenizer(prompt_text, return_tensors="pt").to(device)
    generated_ids = finetuned_model.generate(
        input_ids=inputs["input_ids"],
        max_new_tokens=100,   # Adjust based on query complexity
        temperature=0.1,      # Deterministic output
        num_beams=5,          # Beam search for better output quality
        early_stopping=True,  # Stop early if possible
    )
    generated_sql = tokenizer.decode(generated_ids[0], skip_special_tokens=True)

    # Post-processing to remove repeated text
    generated_sql = generated_sql.split(";")[0] + ";"  # Keep only the first valid SQL query

    return generated_sql

# Sample context and query (example)
context = (
    "CREATE TABLE customers (id INT PRIMARY KEY, name VARCHAR(100), country VARCHAR(50)); "
    "CREATE TABLE orders (order_id INT PRIMARY KEY, customer_id INT, total_amount DECIMAL(10,2), "
    "order_date DATE, FOREIGN KEY (customer_id) REFERENCES customers(id)); "
    "INSERT INTO customers (id, name, country) VALUES (1, 'Alice', 'USA'), (2, 'Bob', 'UK'), "
    "(3, 'Charlie', 'Canada'), (4, 'David', 'USA'); "
    "INSERT INTO orders (order_id, customer_id, total_amount, order_date) VALUES "
    "(101, 1, 500, '2024-01-15'), (102, 2, 300, '2024-01-20'), "
    "(103, 1, 700, '2024-02-10'), (104, 3, 450, '2024-02-15'), "
    "(105, 4, 900, '2024-03-05');"
)
query = (
    "Retrieve the total order amount for each customer, showing only customers from the USA, "
    "and sort the result by total order amount in descending order."
)

# Construct the prompt
sample_prompt = f"""Context:
{context}

Query:
{query}

Response:
"""

logger.info("Running inference with deterministic decoding and beam search.")
generated_sql = run_inference(sample_prompt)

# Print output in the given format
print("Prompt:")
print("Context:")
print(context)
print("\nQuery:")
print(query)
print("\nResponse:")
print(generated_sql)


2025-03-19 16:51:05,225 - INFO - Running inference with deterministic decoding and beam search.


Prompt:
Context:
CREATE TABLE customers (id INT PRIMARY KEY, name VARCHAR(100), country VARCHAR(50)); CREATE TABLE orders (order_id INT PRIMARY KEY, customer_id INT, total_amount DECIMAL(10,2), order_date DATE, FOREIGN KEY (customer_id) REFERENCES customers(id)); INSERT INTO customers (id, name, country) VALUES (1, 'Alice', 'USA'), (2, 'Bob', 'UK'), (3, 'Charlie', 'Canada'), (4, 'David', 'USA'); INSERT INTO orders (order_id, customer_id, total_amount, order_date) VALUES (101, 1, 500, '2024-01-15'), (102, 2, 300, '2024-01-20'), (103, 1, 700, '2024-02-10'), (104, 3, 450, '2024-02-15'), (105, 4, 900, '2024-03-05');

Query:
Retrieve the total order amount for each customer, showing only customers from the USA, and sort the result by total order amount in descending order.

Response:
SELECT customer_id, SUM(total_amount) as total_amount FROM orders JOIN customers ON orders.customer_id = customers.id WHERE customers.country = 'USA' GROUP BY customer_id ORDER BY total_amount DESC;


# Merging and Saving a Fine-Tuned Model with LoRA Adapter

This section of code demonstrates how to save a fine-tuned LoRA adapter separately, merge it into the base model to create a fully fine-tuned model, and then save the complete model along with a generation configuration file. Below is an in-depth explanation of every part of the code:

---

1. ***Defining Paths and Model Identifiers:***

    - ***`base_model_name`:***
        - Specifies the identifier for the pre-trained T5 model provided by Google (`google/flan-t5-base`).

    - ***`lora_model_path`:***
        - Indicates the directory where the fine-tuned LoRA adapter is stored. This adapter contains the additional parameters that were updated during fine-tuning.

    - ***`full_model_output_path`:***
        - Defines the directory where the final merged model (base model with integrated LoRA adapter) will be saved.
        This full model can be used for inference without needing to load the adapter separately.

2. ***Loading the Base Model and Tokenizer:***

    - ***Base Model Loading:***
        - The base T5 model is loaded using `AutoModelForSeq2SeqLM.from_pretrained` with a specified data type (`torch.bfloat16`) to optimize memory usage and computational performance.

    - ***Tokenizer Loading:***
        - The corresponding tokenizer is loaded to ensure that text is pre-processed consistently with the model's requirements.
     
3. ***Loading the Fine-Tuned LoRA Adapter:***

    - ***Purpose:***
        - This line loads the fine-tuned LoRA adapter into the base model. The adapter contains modifications tailored to a specific task (e.g., text-to-SQL) and enables efficient fine-tuning by updating only a small subset of parameters.

    - ***Mechanism:***
        - `PeftModel.from_pretrained` wraps the base model with the fine-tuned LoRA adapter parameters stored at `lora_model_path`.
     
4. ***Saving the LoRA Adapter Separately:***

    - ***Why Save Separately?***
        - Saving the LoRA adapter by itself allows users who need a lightweight model for further fine-tuning or deployment to load only the adapter parameters rather than the entire model.

    - ***Actions:***
        - The LoRA adapter and the associated tokenizer are saved to `lora_model_path` using their respective `save_pretrained` methods.
     
5. ***Merging the LoRA Adapter with the Base Model:***

    - ***Purpose:***
        - The merging process integrates the LoRA adapter parameters into the base model. After merging, the model becomes fully fine-tuned and no longer requires the separate adapter.

    - ***Method:***
        - `merge_and_unload() combines the adapter weights with the base model’s weights and then unloads the adapter, resulting in a standalone, fully fine-tuned model.

6. ***Saving the Fully Merged Fine-Tuned Model:***

    - ***Purpose:***
        - After merging, the complete fine-tuned model (now including the LoRA modifications) is saved to disk for future inference or deployment.

    - ***Actions:***
        - The `save_pretrained` method is called on both the merged model and the tokenizer, storing them at `full_model_output_path`.
     
7. ***Saving the Generation Configuration:***

    - ***Purpose:***
        - Saving a generation configuration is optional but highly recommended. It ensures that inference settings (such as maximum tokens to generate, temperature, beam search settings, etc.) are preserved and can be loaded alongside the model.

    - ***Configuration Details:***
        - ***`max_new_tokens`:***
            - Limits the number of tokens the model will generate in a single inference call.

        - ***`temperature`:***
            - Controls the randomness of predictions; a lower value (0.1) makes the output more deterministic.

        - ***`num_beams`:***
            - Specifies the number of beams used in beam search for more diverse and high-quality generation.

        - ***`early_stopping`:***
            -  Enables stopping the generation process early if certain conditions are met.

    - ***Saving Process:***
        - The configuration dictionary is saved as a JSON file in the model output directory, allowing for easy retrieval during inference



In [16]:
import torch
import json
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer
from peft import PeftModel

# Define paths
base_model_name = "google/flan-t5-base"  # Base model name
lora_model_path = "text2sql_flant5base_finetuned"  # Folder where LoRA adapter is saved
full_model_output_path = "text2sql_flant5base_finetuned_full"  # For merged full model

# Load base model and tokenizer
base_model = AutoModelForSeq2SeqLM.from_pretrained(base_model_name, torch_dtype=torch.bfloat16)
tokenizer = AutoTokenizer.from_pretrained(base_model_name)

# Load fine-tuned LoRA adapter model
lora_model = PeftModel.from_pretrained(base_model, lora_model_path)

# ✅ Save the LoRA adapter separately (for users who want lightweight adapters)
lora_model.save_pretrained(lora_model_path)
tokenizer.save_pretrained(lora_model_path)

# ✅ Merge LoRA into the base model to create a fully fine-tuned model
merged_model = lora_model.merge_and_unload()

# ✅ Save the full fine-tuned model
merged_model.save_pretrained(full_model_output_path)
tokenizer.save_pretrained(full_model_output_path)

# ✅ Save generation config (optional but recommended for inference settings)
generation_config = {
    "max_new_tokens": 100,
    "temperature": 0.1,
    "num_beams": 5,
    "early_stopping": True
}
with open(f"{full_model_output_path}/generation_config.json", "w") as f:
    json.dump(generation_config, f)

print(f"✅ LoRA adapter saved at: {lora_model_path}")
print(f"✅ Fully merged fine-tuned model saved at: {full_model_output_path}")


✅ LoRA adapter saved at: text2sql_flant5base_finetuned
✅ Fully merged fine-tuned model saved at: text2sql_flant5base_finetuned_full


# Inference:

In [17]:
import torch
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer
import logging

# Set up logging
logging.basicConfig(level=logging.INFO, format="%(asctime)s - %(levelname)s - %(message)s")
logger = logging.getLogger(__name__)

# Ensure device is set (GPU if available)
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load the fine-tuned model and tokenizer
model_name = "aarohanverma/text2sql-flan-t5-base-qlora-finetuned"
model = AutoModelForSeq2SeqLM.from_pretrained(model_name, torch_dtype=torch.bfloat16).to(device)
tokenizer = AutoTokenizer.from_pretrained("aarohanverma/text2sql-flan-t5-base-qlora-finetuned")

# Ensure decoder start token is set
if model.config.decoder_start_token_id is None:
    model.config.decoder_start_token_id = tokenizer.pad_token_id

def run_inference(prompt_text: str) -> str:
    """
    Runs inference on the fine-tuned model using beam search with fixes for repetition.
    """
    inputs = tokenizer(prompt_text, return_tensors="pt", truncation=True, max_length=512).to(device)

    generated_ids = model.generate(
        input_ids=inputs["input_ids"],
        decoder_start_token_id=model.config.decoder_start_token_id, 
        max_new_tokens=100,  
        temperature=0.1, 
        num_beams=5, 
        repetition_penalty=1.2,  
        early_stopping=True,  
    )

    generated_sql = tokenizer.decode(generated_ids[0], skip_special_tokens=True)

    # Post-processing to remove repeated text
    generated_sql = generated_sql.split(";")[0] + ";"  # Keep only the first valid SQL query

    return generated_sql

# Example usage:
context = (
    "CREATE TABLE employees (id INT PRIMARY KEY, name VARCHAR(100), department VARCHAR(50), salary INT); "
    "CREATE TABLE projects (project_id INT PRIMARY KEY, project_name VARCHAR(100), budget INT); "
    "CREATE TABLE employee_projects (employee_id INT, project_id INT, role VARCHAR(50), "
    "FOREIGN KEY (employee_id) REFERENCES employees(id), FOREIGN KEY (project_id) REFERENCES projects(project_id)); "
    "INSERT INTO employees (id, name, department, salary) VALUES "
    "(1, 'Alice', 'Engineering', 90000), (2, 'Bob', 'Marketing', 70000), "
    "(3, 'Charlie', 'Engineering', 95000), (4, 'David', 'HR', 60000), (5, 'Eve', 'Engineering', 110000); "
    "INSERT INTO projects (project_id, project_name, budget) VALUES "
    "(101, 'AI Research', 500000), (102, 'Marketing Campaign', 200000), (103, 'Cloud Migration', 300000); "
    "INSERT INTO employee_projects (employee_id, project_id, role) VALUES "
    "(1, 101, 'Lead Engineer'), (2, 102, 'Marketing Specialist'), (3, 101, 'Engineer'), "
    "(4, 103, 'HR Coordinator'), (5, 101, 'AI Scientist');"
)

query = ("Find the names of employees who are working on the 'AI Research' project along with their roles.")



# Construct the prompt
sample_prompt = f"""Context:
{context}

Query:
{query}

Response:
"""

logger.info("Running inference with beam search decoding.")
generated_sql = run_inference(sample_prompt)

print("Prompt:")
print("Context:")
print(context)
print("\nQuery:")
print(query)
print("\nResponse:")
print(generated_sql)

/venv/main/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:629: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`. This was detected when initializing the generation config instance, which means the corresponding file may hold incorrect parameterization and should be fixed.
  warnings.warn(
/venv/main/lib/python3.10/site-packages/transformers/generation/configuration_utils.py:629: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.1` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
2025-03-19 16:51:49,933 - INFO - Running inference with beam search decoding.


Prompt:
Context:
CREATE TABLE employees (id INT PRIMARY KEY, name VARCHAR(100), department VARCHAR(50), salary INT); CREATE TABLE projects (project_id INT PRIMARY KEY, project_name VARCHAR(100), budget INT); CREATE TABLE employee_projects (employee_id INT, project_id INT, role VARCHAR(50), FOREIGN KEY (employee_id) REFERENCES employees(id), FOREIGN KEY (project_id) REFERENCES projects(project_id)); INSERT INTO employees (id, name, department, salary) VALUES (1, 'Alice', 'Engineering', 90000), (2, 'Bob', 'Marketing', 70000), (3, 'Charlie', 'Engineering', 95000), (4, 'David', 'HR', 60000), (5, 'Eve', 'Engineering', 110000); INSERT INTO projects (project_id, project_name, budget) VALUES (101, 'AI Research', 500000), (102, 'Marketing Campaign', 200000), (103, 'Cloud Migration', 300000); INSERT INTO employee_projects (employee_id, project_id, role) VALUES (1, 101, 'Lead Engineer'), (2, 102, 'Marketing Specialist'), (3, 101, 'Engineer'), (4, 103, 'HR Coordinator'), (5, 101, 'AI Scientist');
